<a href="https://colab.research.google.com/github/VrijKun/CS6910_Assignment_1/blob/main/Assignment_1_DL_ED23D015_2nd_Experimants.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install --upgrade wandb

In [ ]:
import wandb
wandb.login() #3c21150eb43b007ee446a1ff6e87f640ec7528c4

wandb: Currently logged in as: ed23d015 (tea_vrij_ed23d015). Use `wandb login --relogin` to force relogin


True

In [ ]:
from keras.datasets import fashion_mnist
import numpy as np
from sklearn.model_selection import train_test_split
from tqdm import tqdm

# Load the Fashion-MNIST dataset
(X_train, Y_train), (X_test, Y_test) = fashion_mnist.load_data()


image_classes = len(np.unique(Y_train)) #to find out number of unique images
image_labels = ['T-shirt/top', 'Trouser', 'Pullover', 'Dress', 'Coat', 'Sandal', 'Shirt', 'Sneaker', 'Bag', 'Ankle boot'] #taken from keras documentation

def show_images(image_classe,img_labels,X,Y):
   set_Labels=[]
   set_Images = []

   for i in range(len(X)):
     if len(set_Images)== image_classes:
       break
     if image_labels[Y[i]] not in set_Labels:

      set_Labels.append(image_labels[Y[i]])
      set_Images.append(X[i])

   run=wandb.init(project='DL_Assignment_1',entity='ed23d015',reinit=True)
   run.log({"Sample from each class":list(wandb.Image(img,caption= caption) for img,caption in zip(set_Images,set_Labels))})
   run.finish()

#Getting prints
show_images(image_classes,image_labels,X_test,Y_test)


wandb: Currently logged in as: ed23d015. Use `wandb login --relogin` to force relogin


In [ ]:
#Class is working as well. KEEP IT

class NurlNtwk:
    def __init__(self, input_layer, hidden_layers, output_layer, initialization, activation, loss_function, optimizer, dropout_rate=0):
        self.input_layer = input_layer
        self.hidden_layers = hidden_layers
        self.output_layer = output_layer
        self.initialization = initialization
        self.activation = activation
        self.loss_function = loss_function
        self.optimizer = optimizer
        self.dropout_rate = dropout_rate
        print()
        self.parameters = None

    def initialize_parameters(self):
        np.random.seed(1)
        parameters = {}
        layer_dims = [self.input_layer] + self.hidden_layers + [self.output_layer]
        L = len(layer_dims)
        for l in range(1, L):
            if self.initialization == "random":
                parameters['W' + str(l)] = np.random.randn(layer_dims[l], layer_dims[l-1]) * 0.01
            elif self.initialization == "Xavier":
                parameters['W' + str(l)] = np.random.randn(layer_dims[l], layer_dims[l-1]) * np.sqrt(1 / layer_dims[l-1])
            parameters['b' + str(l)] = np.zeros((layer_dims[l], 1))
        self.parameters = parameters

    def sigmoid(self, Z):
        return 1 / (1 + np.exp(-Z))

    def relu(self, Z):
        return np.maximum(0, Z)

    def tanh(self, Z):
        return np.tanh(Z)

    def softmax(self, Z):
        exp_Z = np.exp(Z - np.max(Z, axis=0, keepdims=True))
        return exp_Z / np.sum(exp_Z, axis=0, keepdims=True)

    def forward_propagation(self, X):
        caches = []
        A = X
        L = len(self.parameters) // 2
        for l in range(1, L):
            A_prev = A
            Z = np.dot(self.parameters['W' + str(l)], A_prev) + self.parameters['b' + str(l)]
            if self.activation == "sigmoid":
                A = self.sigmoid(Z)
            elif self.activation == "relu":
                A = self.relu(Z)
            elif self.activation == "tanh":
                A = self.tanh(Z)
            cache = (A_prev, self.parameters['W' + str(l)], self.parameters['b' + str(l)], Z)
            caches.append(cache)
        ZL = np.dot(self.parameters['W' + str(L)], A) + self.parameters['b' + str(L)]
        AL = self.softmax(ZL)
        cache = (A, self.parameters['W' + str(L)], self.parameters['b' + str(L)], ZL)
        caches.append(cache)
        return AL, caches

    def compute_cost(self, AL, Y):
        m = Y.shape[1]
        if self.loss_function == "cross_entropy":
            cost = -np.sum(np.multiply(Y, np.log(AL))) / m
        return cost

    def backward_propagation(self, AL, Y, caches):
        grads = {}
        L = len(caches)
        m = AL.shape[1]
        Y = Y.reshape(AL.shape)
        dZL = AL - Y
        A_prev, W, b, Z = caches[L-1]
        grads['dW' + str(L)] = np.dot(dZL, A_prev.T) / m
        grads['db' + str(L)] = np.sum(dZL, axis=1, keepdims=True) / m
        dAL = np.dot(W.T, dZL)
        for l in reversed(range(L-1)):
            A_prev, W, b, Z = caches[l]
            if self.activation == 'relu':
                dZ = dAL.copy()
                dZ[Z <= 0] = 0  # Derivative of ReLU
            elif self.activation == 'sigmoid':
                sigmoid_Z = self.sigmoid(Z)
                dZ = dAL * sigmoid_Z * (1 - sigmoid_Z)  # Derivative of sigmoid
            elif self.activation == 'tanh':
                tanh_Z = self.tanh(Z)
                dZ = dAL * (1 - tanh_Z**2)  # Derivative of tanh
            grads['dW' + str(l + 1)] = np.dot(dZ, A_prev.T) / m
            grads['db' + str(l + 1)] = np.sum(dZ, axis=1, keepdims=True) / m
            dAL = np.dot(W.T, dZ)
        return grads

    def initialize_optimizer(self):
        self.velocity = {}
        self.momentum = 0
        self.rmsprop_cache = {}
        self.adam_params = {'m': {}, 'v': {}}
        self.nadam_params = {'m': {}, 'v': {}}

    def update_parameters(self, grads, learning_rate):
        L = len(self.parameters) // 2
        for l in range(L):
            if self.optimizer == "SGD":
                self.parameters['W' + str(l+1)] -= learning_rate * grads['dW' + str(l+1)]
                self.parameters['b' + str(l+1)] -= learning_rate * grads['db' + str(l+1)]
            elif self.optimizer == "Momentum":
                v_dW = 0.9 * grads['dW' + str(l+1)]
                v_db = 0.9 * grads['db' + str(l+1)]
                self.parameters['W' + str(l+1)] -= learning_rate * v_dW
                self.parameters['b' + str(l+1)] -= learning_rate * v_db
            elif self.optimizer == "Nesterov":
                v_dW = 0.9 * grads['dW' + str(l+1)]
                v_db = 0.9 * grads['db' + str(l+1)]
                self.parameters['W' + str(l+1)] -= learning_rate * (v_dW + 0.9 * v_dW)
                self.parameters['b' + str(l+1)] -= learning_rate * (v_db + 0.9 * v_db)
            elif self.optimizer == "RMSprop":
                s_dW = 0.99 * grads['dW' + str(l+1)]**2 + (1 - 0.99) * (grads['dW' + str(l+1)]**2)
                s_db = 0.99 * grads['db' + str(l+1)]**2 + (1 - 0.99) * (grads['db' + str(l+1)]**2)
                self.parameters['W' + str(l+1)] -= learning_rate * grads['dW' + str(l+1)] / (np.sqrt(s_dW) + (1e-8))
                self.parameters['b' + str(l+1)] -= learning_rate * grads['db' + str(l+1)] / (np.sqrt(s_db) + (1e-8))
            elif self.optimizer == "Adam":
                v_dW = 0.9 * grads['dW' + str(l+1)] + (1 - 0.9) * grads['dW' + str(l+1)]
                v_db = 0.9 * grads['db' + str(l+1)] + (1 - 0.9) * grads['db' + str(l+1)]
                s_dW = 0.99 * grads['dW' + str(l+1)]**2 + (1 - 0.99) * (grads['dW' + str(l+1)]**2)
                s_db = 0.99 * grads['db' + str(l+1)]**2 + (1 - 0.99) * (grads['db' + str(l+1)]**2)
                self.parameters['W' + str(l+1)] -= learning_rate * v_dW / (np.sqrt(s_dW) + (1e-8))
                self.parameters['b' + str(l+1)] -= learning_rate * v_db / (np.sqrt(s_db) + (1e-8))
            elif self.optimizer == "Nadam":
                v_dW = 0.9 * grads['dW' + str(l+1)] + (1 - 0.9) * grads['dW' + str(l+1)]
                v_db = 0.9 * grads['db' + str(l+1)] + (1 - 0.9) * grads['db' + str(l+1)]
                s_dW = 0.99 * grads['dW' + str(l+1)]**2 + (1 - 0.99) * (grads['dW' + str(l+1)]**2)
                s_db = 0.99 * grads['db' + str(l+1)]**2 + (1 - 0.99) * (grads['db' + str(l+1)]**2)
                v_dW_corrected = v_dW / (1 - 0.9)
                v_db_corrected = v_db / (1 - 0.9)
                s_dW_corrected = s_dW / (1 - 0.99)
                s_db_corrected = s_db / (1 - 0.99)
                self.parameters['W' + str(l+1)] -= learning_rate * v_dW_corrected / (np.sqrt(s_dW_corrected) + (1e-8))
                self.parameters['b' + str(l+1)] -= learning_rate * v_db_corrected / (np.sqrt(s_db_corrected) + (1e-8))

    def train(self, X_train, Y_train, X_val, Y_val, num_epochs, learning_rate,batch_size, beta1=0.9, beta2=0.999, epsilon=1e-8, WandB=False):
        train_costs = []
        val_costs = []
        val_acc = []
        train_acc = []
        self.initialize_parameters()

        for epoch in range(int(num_epochs)):
          for batch in range(0, X_train.shape[1], batch_size):

                batch_images =  X_train[:,batch:batch+batch_size]
                batch_output =  train_labels[:,batch:batch+batch_size]
                AL, caches =  self.forward_propagation(batch_images)
                grads = self.backward_propagation(AL, batch_output, caches)

                if self.optimizer == "SGD":
                    self.update_parameters(grads, learning_rate)
                elif self.optimizer == "Momentum":
                    self.update_parameters(grads, learning_rate)
                elif self.optimizer== "Nesterov":
                    self.update_parameters(grads, learning_rate)
                elif self.optimizer == "RMSprop":
                    self.update_parameters(grads, learning_rate)
                elif self.optimizer == "Adam":
                    self.update_parameters(grads, learning_rate)
                elif self.optimizer == "Nadam":
                    self.update_parameters(grads, learning_rate)

          train_predictions = self.predict(X_train)
          val_predictions = self.predict(X_val)
          train_acc = self.accuracy(train_predictions, Y_train)
          val_acc = self.accuracy(val_predictions, Y_val)

          print(f"Epoch {epoch+1}/{num_epochs}, train_acc: {train_acc:.4f}, val_acc: {val_acc:.4f}")

          if WandB:
              wandb.log({"val_accuracy": val_acc,"accuracy": train_acc,"steps":epoch},)
        return train_acc

    def predict(self, X):
        AL, _ = self.forward_propagation(X)
        return np.argmax(AL, axis=0)

    def accuracy(self, predictions, labels):
        return np.mean(predictions == np.argmax(labels, axis=0))


# Load the Fashion-MNIST dataset
(train_images, train_labels), (test_images, test_labels) = fashion_mnist.load_data()

# Preprocess the data
train_images = train_images / 255.0
test_images = test_images / 255.0
train_images = train_images.reshape(train_images.shape[0], -1).T
test_images = test_images.reshape(test_images.shape[0], -1).T

def to_categorical(labels, num_classes):
    # Initialize an array of zeros with shape (num_classes, num_samples)
    one_hot = np.zeros((num_classes, labels.shape[0]))
    # Set the corresponding index of each sample to 1
    one_hot[labels, np.arange(labels.shape[0])] = 1
    return one_hot.T  # Transpose the array to match the desired shape

# Convert labels to one-hot encoding
train_labels = to_categorical(train_labels, num_classes=10).T
test_labels = to_categorical(test_labels, num_classes=10).T

# Split train set into train and validation
val_split = int(train_images.shape[1] * 0.1)
val_images = train_images[:, :val_split]
val_labels = train_labels[:, :val_split]
train_images = train_images[:, val_split:]
train_labels = train_labels[:, val_split:]

'''
# Define hyperparameters
input_layer = train_images.shape[0]
print(input_layer)
hidden_layers = [64,64,64,64,64]
output_layer = 10
initialization = "Xavier"
activation = "tanh"
loss_function = "cross_entropy"
dropout_rate = 0.0
learning_rate = 0.0001
num_epochs = 10
optimizer = "Adam"
batch_size = 128
# Create and train the network
network = NurlNtwk(input_layer, hidden_layers, output_layer, initialization, activation, loss_function, optimizer, dropout_rate)
train_acc = network.train(train_images, train_labels, val_images, val_labels, num_epochs, batch_size =batch_size, learning_rate=learning_rate)
# Evaluate the model
train_predictions = network.predict(train_images)
val_predictions = network.predict(val_images)
train_acc = network.accuracy(train_predictions, train_labels)
val_acc = network.accuracy(val_predictions, val_labels)
print(f"Train Accuracy: {train_acc:.4f}")
print(f"Validation Accuracy: {val_acc:.4f}")'''

'\n# Define hyperparameters\ninput_layer = train_images.shape[0]\nprint(input_layer)\nhidden_layers = [64,64,64,64,64]\noutput_layer = 10\ninitialization = "Xavier"\nactivation = "tanh"\nloss_function = "cross_entropy"\ndropout_rate = 0.0\nlearning_rate = 0.0001\nnum_epochs = 10\noptimizer = "Adam"\nbatch_size = 128\n# Create and train the network\nnetwork = NurlNtwk(input_layer, hidden_layers, output_layer, initialization, activation, loss_function, optimizer, dropout_rate)\ntrain_acc = network.train(train_images, train_labels, val_images, val_labels, num_epochs, batch_size =batch_size, learning_rate=learning_rate)\n# Evaluate the model\ntrain_predictions = network.predict(train_images)\nval_predictions = network.predict(val_images)\ntrain_acc = network.accuracy(train_predictions, train_labels)\nval_acc = network.accuracy(val_predictions, val_labels)\nprint(f"Train Accuracy: {train_acc:.4f}")\nprint(f"Validation Accuracy: {val_acc:.4f}")'

In [ ]:
sweep_config = {
    'method': 'bayes', #grid, random,bayes
    'metric': {
      'name': 'val_accuracy',
      'goal': 'maximize'
    },
    'parameters': {
        'num_epochs': {
            'values': [5,10]
        },
        'learning_rate': {
            'values': [0.001,0.0001]
        },
        'loss_function':{
            'values':['cross_entropy']
        },
        'initialisation':{
            'values':['random','Xavier']
        },
        'batch_size':{
            'values':[32,64,128]
        },
        'optimiser': {
            'values': ['SGD','Momentum','Nesterov', 'RMSprop','Adam','Nadam']
        },
        'activation': {
            'values': ['relu', 'sigmoid', 'tanh']
        },
        'hidden_layer': {
            'values': [
                       [64,64,64],[128,128,128],[32,32,32],
                       [64,64,64,64],[64,64,64,64,64],
                       [128,128,128,128],[128,128,128,128,128]]
        },

        'weight_decay':{
            'values':[0.0005,0.5]
        },
        'dropout_rate':{
          'values':[0]
        }

    }
}


sweep_id = wandb.sweep(sweep_config, entity='ed23d015', project="DL_Assignment_1")

def train1():
  steps = 10
  # Default values for hyper-parameters we're going to sweep over
  config_defaults = {
      'num_epochs': 5,
      'input_layer': 784,
      'output_layer': 10,
      'batch_size':64,
      'dropout_rate':0,
      'weight_decay':0.005,
      'learning_rate': 0.0001,
      'hidden_layer':[16,16,16],
      'optimiser':'SGD',
      'activation':'sigmoid',
      'initialisation':'Xavier',
      'loss_function':'cross_entropy'

  }

  # Initialize a new wandb run
  wandb.init(project='DL_Assignment_1', entity='ed23d015',config=config_defaults)
  wandb.run.name = 'b_s:'+str(wandb.config.batch_size)+',lr:'+ str(wandb.config.learning_rate)+'drop:'+str(wandb.config.dropout_rate)+',ep:'+str(wandb.config.num_epochs)+ ',opt:'+str(wandb.config.optimiser)+ ',hl:'+str(wandb.config.hidden_layer)+ ',act:'+str(wandb.config.activation)+',decay:'+str(wandb.config.weight_decay)+',init:'+str(wandb.config.initialisation)+',loss:'+str(wandb.config.loss_function)


  config = wandb.config
  learning_rate = config.learning_rate
  num_epochs = int(config.num_epochs)
  hidden_layer = config.hidden_layer
  activation = config.activation
  optimiser = config.optimiser
  input_layer = config.input_layer
  output_layer = config.output_layer
  batch_size = config.batch_size
  weight_decay = config.weight_decay
  loss_function = config.loss_function
  initialisation = config.initialisation
  dropout_rate=config.dropout_rate
  # Model training here
  sweep_network    = NurlNtwk(input_layer, hidden_layer, output_layer,initialization=initialisation,activation=activation,loss_function=loss_function,optimizer=optimiser,dropout_rate=dropout_rate)
  acc1  = sweep_network.train(train_images, train_labels, val_images, val_labels, num_epochs=num_epochs, batch_size = batch_size, learning_rate=learning_rate, WandB=True)

import warnings
warnings.filterwarnings("ignore", category=np.VisibleDeprecationWarning)
wandb.agent(sweep_id, function=train1)


Create sweep with ID: fcbufrpi
Sweep URL: https://wandb.ai/ed23d015/DL_Assignment_1/sweeps/fcbufrpi


wandb: Agent Starting Run: oc68ysyy with config:
wandb: 	activation: relu
wandb: 	batch_size: 32
wandb: 	dropout_rate: 0
wandb: 	hidden_layer: [128, 128, 128, 128]
wandb: 	initialisation: random
wandb: 	learning_rate: 0.0001
wandb: 	loss_function: cross_entropy
wandb: 	num_epochs: 10
wandb: 	optimiser: SGD
wandb: 	weight_decay: 0.5
wandb: WARNING Ignored wandb.init() arg project when running a sweep.
wandb: WARNING Ignored wandb.init() arg entity when running a sweep.



Epoch 1/10, train_acc: 0.1007, val_acc: 0.0933
Epoch 2/10, train_acc: 0.1007, val_acc: 0.0933
Epoch 3/10, train_acc: 0.1007, val_acc: 0.0933
Epoch 4/10, train_acc: 0.1007, val_acc: 0.0933
Epoch 5/10, train_acc: 0.1007, val_acc: 0.0933
Epoch 6/10, train_acc: 0.1007, val_acc: 0.0933
Epoch 7/10, train_acc: 0.1007, val_acc: 0.0933
Epoch 8/10, train_acc: 0.1007, val_acc: 0.0933
Epoch 9/10, train_acc: 0.1007, val_acc: 0.0933
Epoch 10/10, train_acc: 0.1007, val_acc: 0.0933


wandb: Agent Starting Run: dbjio0h4 with config:
wandb: 	activation: sigmoid
wandb: 	batch_size: 32
wandb: 	dropout_rate: 0
wandb: 	hidden_layer: [32, 32, 32]
wandb: 	initialisation: random
wandb: 	learning_rate: 0.001
wandb: 	loss_function: cross_entropy
wandb: 	num_epochs: 10
wandb: 	optimiser: Adam
wandb: 	weight_decay: 0.0005
wandb: WARNING Ignored wandb.init() arg project when running a sweep.
wandb: WARNING Ignored wandb.init() arg entity when running a sweep.



Epoch 1/10, train_acc: 0.3720, val_acc: 0.3738
Epoch 2/10, train_acc: 0.5969, val_acc: 0.6043
Epoch 3/10, train_acc: 0.6887, val_acc: 0.6940
Epoch 4/10, train_acc: 0.6976, val_acc: 0.7008
Epoch 5/10, train_acc: 0.7041, val_acc: 0.7102
Epoch 6/10, train_acc: 0.7033, val_acc: 0.7092
Epoch 7/10, train_acc: 0.7252, val_acc: 0.7265
Epoch 8/10, train_acc: 0.7496, val_acc: 0.7507
Epoch 9/10, train_acc: 0.7505, val_acc: 0.7490
Epoch 10/10, train_acc: 0.7765, val_acc: 0.7713


...


Epoch 1/10, train_acc: 0.7721, val_acc: 0.7747
Epoch 2/10, train_acc: 0.8146, val_acc: 0.8148
Epoch 3/10, train_acc: 0.8288, val_acc: 0.8313
Epoch 4/10, train_acc: 0.8361, val_acc: 0.8393
Epoch 5/10, train_acc: 0.8421, val_acc: 0.8460
Epoch 6/10, train_acc: 0.8461, val_acc: 0.8493
Epoch 7/10, train_acc: 0.8493, val_acc: 0.8507
Epoch 8/10, train_acc: 0.8522, val_acc: 0.8533
Epoch 9/10, train_acc: 0.8549, val_acc: 0.8550
Epoch 10/10, train_acc: 0.8566, val_acc: 0.8558


wandb: Sweep Agent: Waiting for job.
wandb: Job received.
wandb: Agent Starting Run: ur0an5d1 with config:
wandb: 	activation: tanh
wandb: 	batch_size: 32
wandb: 	dropout_rate: 0
wandb: 	hidden_layer: [128, 128, 128]
wandb: 	initialisation: Xavier
wandb: 	learning_rate: 0.001
wandb: 	loss_function: cross_entropy
wandb: 	num_epochs: 10
wandb: 	optimiser: Nadam
wandb: 	weight_decay: 0.0005
wandb: WARNING Ignored wandb.init() arg project when running a sweep.
wandb: WARNING Ignored wandb.init() arg entity when running a sweep.



Epoch 1/10, train_acc: 0.8336, val_acc: 0.8292
Epoch 2/10, train_acc: 0.8476, val_acc: 0.8432
Epoch 3/10, train_acc: 0.8528, val_acc: 0.8437
Epoch 4/10, train_acc: 0.8547, val_acc: 0.8433
Epoch 5/10, train_acc: 0.8609, val_acc: 0.8490
Epoch 6/10, train_acc: 0.8632, val_acc: 0.8523
Epoch 7/10, train_acc: 0.8658, val_acc: 0.8517
Epoch 8/10, train_acc: 0.8628, val_acc: 0.8492
Epoch 9/10, train_acc: 0.8720, val_acc: 0.8615
Epoch 10/10, train_acc: 0.8713, val_acc: 0.8587


wandb: Agent Starting Run: pxrb5kik with config:
wandb: 	activation: sigmoid
wandb: 	batch_size: 32
wandb: 	dropout_rate: 0
wandb: 	hidden_layer: [64, 64, 64]
wandb: 	initialisation: Xavier
wandb: 	learning_rate: 0.001
wandb: 	loss_function: cross_entropy
wandb: 	num_epochs: 10
wandb: 	optimiser: Nadam
wandb: 	weight_decay: 0.0005
wandb: WARNING Ignored wandb.init() arg project when running a sweep.
wandb: WARNING Ignored wandb.init() arg entity when running a sweep.



Epoch 1/10, train_acc: 0.7994, val_acc: 0.8000
Epoch 2/10, train_acc: 0.8201, val_acc: 0.8205
Epoch 3/10, train_acc: 0.8269, val_acc: 0.8248
Epoch 4/10, train_acc: 0.8324, val_acc: 0.8298
Epoch 5/10, train_acc: 0.8381, val_acc: 0.8327
Epoch 6/10, train_acc: 0.8387, val_acc: 0.8338
Epoch 7/10, train_acc: 0.8394, val_acc: 0.8340
Epoch 8/10, train_acc: 0.8429, val_acc: 0.8343
